In [5]:
import sys
sys.path.insert(0, '../')

import pandas as pd
from sklearn import metrics
#from keras.wrappers.scikit_learn import KerasClassifier
from classification_plots import plot_confusion_matrix
import matplotlib.pyplot as plt
import os
from collections import Counter
import numpy as np
import scipy 
%matplotlib notebook
import shutil
from scipy.io import loadmat

In [6]:
os.environ["CUDA_VISIBLE_DEVICES"]="0"
import warnings
warnings.filterwarnings('ignore')
os.environ["CUDA_LAUNCH_BLOCKING"]="1"

In [7]:
audio_dir = '../../ESC-50/audio/'
path_to_db='../../ESC-50/'

In [8]:
from torch.utils.data import Dataset, DataLoader
class audiotrainset(Dataset):
    def __init__(self):
        root = "./class_audio/"
        self.data_list = []
        self.label_list = []
        for root, dir, files in os.walk("./class_audio/"):
            for file in files:
                if file.find('.mat')!= -1:
#                     print(os.path.join(root, file))
#                     print(int(root[13:]))
                    mdict = loadmat(os.path.join(root, file))
                    data = mdict['file_mfcc_features']
                    labels = mdict['label']
                    self.data_list.append(data)
                    self.label_list.append(labels)
        print(len(self.data_list), len(self.label_list))
        
    def __len__(self):
        return len(self.data_list)

    def __getitem__(self, index):

        data = self.data_list[index]
        label= self.label_list[index] 
        data = np.asarray(data)
        data_infs = np.where(np.isinf(data))
        data[data_infs] = 0
        data_nans = np.where(np.isnan(data))
        data[data_nans] = 0
        label = np.asarray(label[0][0])
        data = data.reshape((data.shape[1],))
        return data, label
audiodataloader = audiotrainset()
data,label = audiodataloader.__getitem__(869)
print(data)
print(label)

2000 2000
[ 6.07562151  1.98843673  2.8523851   0.64035995  0.61181615  0.4502217
 -0.11627991 -1.21898821  0.18506928 -0.09253136 -0.25905592  0.29766787
  0.24392305  0.22341602]
28


In [9]:
import torch.nn as nn
import torch.nn.functional as F
class SpectralNet(nn.Module):
    def __init__(self,):
        super(SpectralNet, self).__init__()
        self.fc1 = nn.Linear(14,40)
        self.fc2 = nn.Linear(40,40)
        self.fc3 = nn.Linear(40,40)
        self.fc4 = nn.Linear(40,50)
        self.softmax = nn.Softmax(dim = 1)
        self.batchnorm = nn.BatchNorm1d(40)

    def forward(self, x):
        x = self.fc1(x)
        x = self.batchnorm(x)
        x = F.relu(x)
        x = self.fc2(x)
        x = self.batchnorm(x)
        x = F.relu(x)
        x = self.fc3(x)
        x = self.batchnorm(x)
        x = F.relu(x)
        x = self.fc4(x)
        x = self.softmax(x)
        return x

model = SpectralNet()
print (model)
model.cuda()

SpectralNet(
  (fc1): Linear(in_features=14, out_features=40, bias=True)
  (fc2): Linear(in_features=40, out_features=40, bias=True)
  (fc3): Linear(in_features=40, out_features=40, bias=True)
  (fc4): Linear(in_features=40, out_features=50, bias=True)
  (softmax): Softmax(dim=1)
  (batchnorm): BatchNorm1d(40, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
)


SpectralNet(
  (fc1): Linear(in_features=14, out_features=40, bias=True)
  (fc2): Linear(in_features=40, out_features=40, bias=True)
  (fc3): Linear(in_features=40, out_features=40, bias=True)
  (fc4): Linear(in_features=40, out_features=50, bias=True)
  (softmax): Softmax(dim=1)
  (batchnorm): BatchNorm1d(40, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
)

In [10]:
import torch.optim as optim
import torch
from torch.utils.data.sampler import SubsetRandomSampler
import time

device = 0
criterion = nn.CrossEntropyLoss()
optimizer = optim.SGD(model.parameters(), lr=0.01, momentum=0.7)

validation_split = .25
random_seed= 42
shuffle_dataset = True
dataset_size = 2000
indices = list(range(dataset_size))
split = int(np.floor(validation_split * dataset_size))
if shuffle_dataset :
    np.random.seed(random_seed)
    np.random.shuffle(indices)
train_indices, val_indices = indices[split:], indices[:split]

# Creating PT data samplers and loaders:
train_sampler = SubsetRandomSampler(train_indices)
valid_sampler = SubsetRandomSampler(val_indices)

dataset  = audiotrainset()
trainloader = torch.utils.data.DataLoader(dataset, batch_size=128, 
                                           sampler=train_sampler,pin_memory=True)
valloader = torch.utils.data.DataLoader(dataset, batch_size=128,
                                                sampler=valid_sampler,pin_memory=True)

val_history = []
val_loss_hist = []
train_history = []
train_loss_hist = []

for epoch in range(15000):  # loop over the dataset multiple times
    
    count = 0
    running_accuracy = 0.0
    running_loss = 0.0
    t1 = time.time()
    for i, data in enumerate(valloader, 0):
        count += 1
        inputs, labels = data
        inputs = inputs.float().to(device)
        labels = labels.long().to(device)
        outputs = model(inputs)
        val_loss = criterion(outputs, labels)
        _, preds = torch.max(outputs, 1)
        acc_val = torch.eq(preds, labels).float().mean()
        running_accuracy += acc_val.item()
        running_loss += val_loss.item()
        
        
    running_accuracy = running_accuracy/count
    running_loss = running_loss/count
    val_history.append(running_accuracy)
    val_loss_hist.append(running_loss)
    t2 = time.time()
    print("===========Phase: Val============")
    print("Validation Time: {}".format(t2 - t1))
    print("Epoch: {}  val_loss: {}".format(epoch, running_loss))
    print("Epoch: {}  val_accuracy: {}".format(epoch, running_accuracy))
    
    
    #### Training #####
    running_loss = 0.0
    count = 0
    running_accuracy = 0
    t1 = time.time()
    for i, data in enumerate(trainloader, 0):
        count += 1
        inputs, labels = data
        inputs = inputs.float()
        inputs = inputs.float().to(device)
        labels = labels.long().to(device)
        optimizer.zero_grad()
        outputs = model(inputs)
        loss = criterion(outputs, labels)
        loss.backward()
        optimizer.step()
        

        running_loss +=  loss.item()
        _, preds = torch.max(outputs, 1)
        acc_train = torch.eq(preds, labels).float().mean()
        running_accuracy += acc_train.item()
        
    
    running_accuracy /= count
    running_loss /= count
    train_history.append(running_accuracy)
    train_loss_hist.append(running_loss)
    t2 = time.time()
    print("===========Phase: Train============") 
    print("Training Time: {}".format(t2 - t1))
    print("Epoch: {}  train_loss: {}".format(epoch, running_loss))
    print("Epoch: {}  train_accuracy: {}".format(epoch, running_accuracy))
    print()
        
print('Finished Training')


2000 2000
===========Phase: Val============
Validation Time: 2.6552979946136475
Epoch: 0  val_loss: 3.9125664234161377
Epoch: 0  val_accuracy: 0.026400862261652946
===========Phase: Train============
Training Time: 0.1655569076538086
Epoch: 0  train_loss: 3.9120832482973733
Epoch: 0  train_accuracy: 0.015625

===========Phase: Val============
Validation Time: 0.034888267517089844
Epoch: 1  val_loss: 3.9125260710716248
Epoch: 1  val_accuracy: 0.024043641984462738
===========Phase: Train============
Training Time: 0.1635596752166748
Epoch: 1  train_loss: 3.9121593236923218
Epoch: 1  train_accuracy: 0.009765625

===========Phase: Val============
Validation Time: 0.033908843994140625
Epoch: 2  val_loss: 3.9122856855392456
Epoch: 2  val_accuracy: 0.026198814623057842
===========Phase: Train============
Training Time: 0.15658068656921387
Epoch: 2  train_loss: 3.91202849149704
Epoch: 2  train_accuracy: 0.013671875

===========Phase: Val============
Validation Time: 0.03690052032470703
Epoch: 

===========Phase: Val============
Validation Time: 0.03291130065917969
Epoch: 26  val_loss: 3.908781588077545
Epoch: 26  val_accuracy: 0.03596443962305784
===========Phase: Train============
Training Time: 0.1561429500579834
Epoch: 26  train_loss: 3.9074191053708396
Epoch: 26  train_accuracy: 0.046591938473284245

===========Phase: Val============
Validation Time: 0.030916929244995117
Epoch: 27  val_loss: 3.908377528190613
Epoch: 27  val_accuracy: 0.03596443962305784
===========Phase: Train============
Training Time: 0.1600804328918457
Epoch: 27  train_loss: 3.906806151072184
Epoch: 27  train_accuracy: 0.04591259049872557

===========Phase: Val============
Validation Time: 0.03390860557556152
Epoch: 28  val_loss: 3.9085588455200195
Epoch: 28  val_accuracy: 0.03987068962305784
===========Phase: Train============
Training Time: 0.168548583984375
Epoch: 28  train_loss: 3.9068254828453064
Epoch: 28  train_accuracy: 0.051517210279901825

===========Phase: Val============
Validation Time: 0.

Epoch: 51  train_accuracy: 0.05310235513995091

===========Phase: Val============
Validation Time: 0.02991962432861328
Epoch: 52  val_loss: 3.904914975166321
Epoch: 52  val_accuracy: 0.03401131462305784
===========Phase: Train============
Training Time: 0.15260529518127441
Epoch: 52  train_loss: 3.901121437549591
Epoch: 52  train_accuracy: 0.056867074221372604

===========Phase: Val============
Validation Time: 0.036900997161865234
Epoch: 53  val_loss: 3.904570519924164
Epoch: 53  val_accuracy: 0.03771551698446274
===========Phase: Train============
Training Time: 0.16706514358520508
Epoch: 53  train_loss: 3.9005565444628396
Epoch: 53  train_accuracy: 0.051007699221372604

===========Phase: Val============
Validation Time: 0.03390836715698242
Epoch: 54  val_loss: 3.9046369194984436
Epoch: 54  val_accuracy: 0.046538254246115685
===========Phase: Train============
Training Time: 0.14560890197753906
Epoch: 54  train_loss: 3.9017328222592673
Epoch: 54  train_accuracy: 0.05414968294401964



Epoch: 77  train_loss: 3.899343729019165
Epoch: 77  train_accuracy: 0.06037703839441141

===========Phase: Val============
Validation Time: 0.03291130065917969
Epoch: 78  val_loss: 3.9030301570892334
Epoch: 78  val_accuracy: 0.04377693962305784
===========Phase: Train============
Training Time: 0.15860319137573242
Epoch: 78  train_loss: 3.8990907073020935
Epoch: 78  train_accuracy: 0.056357563473284245

===========Phase: Val============
Validation Time: 0.027924060821533203
Epoch: 79  val_loss: 3.903284728527069
Epoch: 79  val_accuracy: 0.04748114198446274
===========Phase: Train============
Training Time: 0.15159392356872559
Epoch: 79  train_loss: 3.8993889888127646
Epoch: 79  train_accuracy: 0.061141304671764374

===========Phase: Val============
Validation Time: 0.030911922454833984
Epoch: 80  val_loss: 3.903343617916107
Epoch: 80  val_accuracy: 0.04182381462305784
===========Phase: Train============
Training Time: 0.1575779914855957
Epoch: 80  train_loss: 3.898926397164663
Epoch: 8

===========Phase: Train============
Training Time: 0.16057085990905762
Epoch: 103  train_loss: 3.8964721957842507
Epoch: 103  train_accuracy: 0.06923686588803928

===========Phase: Val============
Validation Time: 0.03390812873840332
Epoch: 104  val_loss: 3.9014883041381836
Epoch: 104  val_accuracy: 0.054350754246115685
===========Phase: Train============
Training Time: 0.15658068656921387
Epoch: 104  train_loss: 3.8957132697105408
Epoch: 104  train_accuracy: 0.06286798013995092

===========Phase: Val============
Validation Time: 0.03490614891052246
Epoch: 105  val_loss: 3.901236355304718
Epoch: 105  val_accuracy: 0.04573006462305784
===========Phase: Train============
Training Time: 0.16008448600769043
Epoch: 105  train_loss: 3.8953158060709634
Epoch: 105  train_accuracy: 0.06884058006107807

===========Phase: Val============
Validation Time: 0.029918193817138672
Epoch: 106  val_loss: 3.9010382294654846
Epoch: 106  val_accuracy: 0.05219558160752058
===========Phase: Train============


...

Epoch: 14877  val_accuracy: 0.24474676698446274
===========Phase: Train============
Training Time: 0.15657997131347656
Epoch: 14877  train_loss: 3.3767409920692444
Epoch: 14877  train_accuracy: 0.5700011352698008

===========Phase: Val============
Validation Time: 0.026926755905151367
Epoch: 14878  val_loss: 3.7085476517677307
Epoch: 14878  val_accuracy: 0.24003232643008232
===========Phase: Train============
Training Time: 0.14760351181030273
Epoch: 14878  train_loss: 3.3813214898109436
Epoch: 14878  train_accuracy: 0.5666610052188238

===========Phase: Val============
Validation Time: 0.027926206588745117
Epoch: 14879  val_loss: 3.702299177646637
Epoch: 14879  val_accuracy: 0.24824891984462738
===========Phase: Train============
Training Time: 0.15259099006652832
Epoch: 14879  train_loss: 3.376474400361379
Epoch: 14879  train_accuracy: 0.5697180728117625

===========Phase: Val============
Validation Time: 0.030918121337890625
Epoch: 14880  val_loss: 3.7208816409111023
Epoch: 14880  v

Epoch: 14902  val_accuracy: 0.22811153158545494
===========Phase: Train============
Training Time: 0.15059638023376465
Epoch: 14902  train_loss: 3.376508275667826
Epoch: 14902  train_accuracy: 0.5697746823231379

===========Phase: Val============
Validation Time: 0.03091716766357422
Epoch: 14903  val_loss: 3.7176275849342346
Epoch: 14903  val_accuracy: 0.22710129246115685
===========Phase: Train============
Training Time: 0.14760446548461914
Epoch: 14903  train_loss: 3.3757415215174356
Epoch: 14903  train_accuracy: 0.5705389479796091

===========Phase: Val============
Validation Time: 0.033908843994140625
Epoch: 14904  val_loss: 3.712173640727997
Epoch: 14904  val_accuracy: 0.23067079484462738
===========Phase: Train============
Training Time: 0.15259099006652832
Epoch: 14904  train_loss: 3.380888263384501
Epoch: 14904  train_accuracy: 0.5687273542086283

===========Phase: Val============
Validation Time: 0.03291130065917969
Epoch: 14905  val_loss: 3.7054723501205444
Epoch: 14905  val_

Epoch: 14927  val_accuracy: 0.22966055944561958
===========Phase: Train============
Training Time: 0.1655569076538086
Epoch: 14927  train_loss: 3.380056083202362
Epoch: 14927  train_accuracy: 0.566802536447843

===========Phase: Val============
Validation Time: 0.02792501449584961
Epoch: 14928  val_loss: 3.711613953113556
Epoch: 14928  val_accuracy: 0.23828125
===========Phase: Train============
Training Time: 0.15558314323425293
Epoch: 14928  train_loss: 3.3777910470962524
Epoch: 14928  train_accuracy: 0.5687273542086283

===========Phase: Val============
Validation Time: 0.03194451332092285
Epoch: 14929  val_loss: 3.7123159766197205
Epoch: 14929  val_accuracy: 0.2392914891242981
===========Phase: Train============
Training Time: 0.15658068656921387
Epoch: 14929  train_loss: 3.379261612892151
Epoch: 14929  train_accuracy: 0.568359375

===========Phase: Val============
Validation Time: 0.02692866325378418
Epoch: 14930  val_loss: 3.715712785720825
Epoch: 14930  val_accuracy: 0.233768858

===========Phase: Train============
Training Time: 0.15061235427856445
Epoch: 14952  train_loss: 3.377097944418589
Epoch: 14952  train_accuracy: 0.5697463800509771

===========Phase: Val============
Validation Time: 0.027925729751586914
Epoch: 14953  val_loss: 3.7122519612312317
Epoch: 14953  val_accuracy: 0.2411772608757019
===========Phase: Train============
Training Time: 0.14511919021606445
Epoch: 14953  train_loss: 3.373388409614563
Epoch: 14953  train_accuracy: 0.5737375468015671

===========Phase: Val============
Validation Time: 0.028921842575073242
Epoch: 14954  val_loss: 3.707094132900238
Epoch: 14954  val_accuracy: 0.23895473778247833
===========Phase: Train============
Training Time: 0.16655325889587402
Epoch: 14954  train_loss: 3.3754512468973794
Epoch: 14954  train_accuracy: 0.5720674842596054

===========Phase: Val============
Validation Time: 0.03390979766845703
Epoch: 14955  val_loss: 3.715398848056793
Epoch: 14955  val_accuracy: 0.22831357643008232
===========Phase: T

===========Phase: Train============
Training Time: 0.1655569076538086
Epoch: 14977  train_loss: 3.378186027208964
Epoch: 14977  train_accuracy: 0.5692651718854904

===========Phase: Val============
Validation Time: 0.025930404663085938
Epoch: 14978  val_loss: 3.720212161540985
Epoch: 14978  val_accuracy: 0.2294585108757019
===========Phase: Train============
Training Time: 0.15159392356872559
Epoch: 14978  train_loss: 3.37682314713796
Epoch: 14978  train_accuracy: 0.5689821094274521

===========Phase: Val============
Validation Time: 0.02991962432861328
Epoch: 14979  val_loss: 3.7059165835380554
Epoch: 14979  val_accuracy: 0.24474676698446274
===========Phase: Train============
Training Time: 0.15059733390808105
Epoch: 14979  train_loss: 3.382339040438334
Epoch: 14979  train_accuracy: 0.5653306146462759

===========Phase: Val============
Validation Time: 0.028921842575073242
Epoch: 14980  val_loss: 3.716363787651062
Epoch: 14980  val_accuracy: 0.23417295143008232
===========Phase: Trai